In [66]:
!pip install kafka-python


[notice] A new release of pip is available: 24.0 -> 24.3.1
[notice] To update, run: C:\Users\Rishita\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [67]:
!pip install pyspark


[notice] A new release of pip is available: 24.0 -> 24.3.1
[notice] To update, run: C:\Users\Rishita\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [68]:
!pip install numpy


[notice] A new release of pip is available: 24.0 -> 24.3.1
[notice] To update, run: C:\Users\Rishita\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [69]:
!pip install pandas


[notice] A new release of pip is available: 24.0 -> 24.3.1
[notice] To update, run: C:\Users\Rishita\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [70]:
!pip install plotly


[notice] A new release of pip is available: 24.0 -> 24.3.1
[notice] To update, run: C:\Users\Rishita\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [71]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
from kafka import KafkaProducer
from pyspark.sql import SparkSession, Row
from pyspark.sql.types import DoubleType
from pyspark.sql.functions import rand, randn, mean, stddev, to_date, col, when, dayofyear, row_number
from pyspark.sql.functions import lit, sum as _sum, udf, hour, collect_list, struct, from_json, avg
from datetime import datetime, timedelta
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.regression import LinearRegression
import json
import random
import time
import csv
import plotly.graph_objs as go
from plotly.subplots import make_subplots
from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml import Pipeline
from pyspark.sql.types import StructType, StructField, StringType, DoubleType
from pyspark.sql.window import Window

In [72]:
!java -version

java version "11.0.24" 2024-07-16 LTS
Java(TM) SE Runtime Environment 18.9 (build 11.0.24+7-LTS-271)
Java HotSpot(TM) 64-Bit Server VM 18.9 (build 11.0.24+7-LTS-271, mixed mode)


In [73]:
!pip install findspark


[notice] A new release of pip is available: 24.0 -> 24.3.1
[notice] To update, run: C:\Users\Rishita\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [74]:
spark = SparkSession \
    .builder \
    .appName("Kafka Integration") \
    .getOrCreate()

spark


In [75]:
spark.version

'3.5.3'

In [76]:
spark

# Part 1 -> Day wise cost consumption on devices

# Data Generation

## Using the pre existing data for 4 months for Delhi city

In [77]:
df = spark.read.csv('C:\\Users\\Rishita\\Desktop\\Rishita Desktop Copy\\IoT_DA331_Project\\DailyDelhiClimateTrain.csv', header=True, inferSchema=True)
df.show()

+----------+------------------+------------------+------------------+------------------+
|      date|          meantemp|          humidity|        wind_speed|      meanpressure|
+----------+------------------+------------------+------------------+------------------+
|2013-01-01|              10.0|              84.5|               0.0|1015.6666666666666|
|2013-01-02|               7.4|              92.0|              2.98|            1017.8|
|2013-01-03| 7.166666666666667|              87.0| 4.633333333333334|1018.6666666666666|
|2013-01-04| 8.666666666666666| 71.33333333333333|1.2333333333333334|1017.1666666666666|
|2013-01-05|               6.0| 86.83333333333333|3.6999999999999997|            1016.5|
|2013-01-06|               7.0|              82.8|              1.48|            1018.0|
|2013-01-07|               7.0|              78.6|               6.3|            1020.0|
|2013-01-08| 8.857142857142858|63.714285714285715| 7.142857142857143|1018.7142857142857|
|2013-01-09|         

#### will now do producer to consumer 

## Keeping only the temperature and humidity columns

In [78]:
df = df.drop("meanpressure","wind_speed")
df.show()

+----------+------------------+------------------+
|      date|          meantemp|          humidity|
+----------+------------------+------------------+
|2013-01-01|              10.0|              84.5|
|2013-01-02|               7.4|              92.0|
|2013-01-03| 7.166666666666667|              87.0|
|2013-01-04| 8.666666666666666| 71.33333333333333|
|2013-01-05|               6.0| 86.83333333333333|
|2013-01-06|               7.0|              82.8|
|2013-01-07|               7.0|              78.6|
|2013-01-08| 8.857142857142858|63.714285714285715|
|2013-01-09|              14.0|             51.25|
|2013-01-10|              11.0|              62.0|
|2013-01-11|15.714285714285714|51.285714285714285|
|2013-01-12|              14.0|              74.0|
|2013-01-13|15.833333333333334| 75.16666666666667|
|2013-01-14|12.833333333333334| 88.16666666666667|
|2013-01-15|14.714285714285714| 71.85714285714286|
|2013-01-16|13.833333333333334| 86.66666666666667|
|2013-01-17|              16.5|

In [79]:
df.count()

1462

In [80]:
stats = df.select(
    mean(df.humidity).alias("mean_humidity"),
    stddev(df.humidity).alias("stddev_humidity")
).collect()

mean_humidity = stats[0]['mean_humidity']
stddev_humidity = stats[0]['stddev_humidity']

In [81]:
mean_humidity, stddev_humidity

(60.77170158004638, 16.769652268485313)

## Linear regression on the given data to generate more data -> year 2017 -> 1 to 5 months data generated using linear regression

In [82]:
# Convert the 'date' column to actual date type (assuming date format is 'YYYY-MM-DD')
df = df.withColumn('date', to_date(df.date, 'yyyy-MM-dd'))

# Prepare features using VectorAssembler
assembler = VectorAssembler(inputCols=["humidity"], outputCol="features")
df_assembled = assembler.transform(df)

# Assume 'meantemp' is the label column
df_assembled = df_assembled.select('date', 'features', 'meantemp')

In [83]:
# Split the data into training and testing (assuming you use all data for training here)
train_data = df_assembled  # As this is a simulation, we'll assume all the data is for training

# Apply Linear Regression
linear_reg = LinearRegression(featuresCol='features', labelCol='meantemp')
model = linear_reg.fit(train_data)


In [84]:
df_assembled.show()

+----------+--------------------+------------------+
|      date|            features|          meantemp|
+----------+--------------------+------------------+
|2013-01-01|              [84.5]|              10.0|
|2013-01-02|              [92.0]|               7.4|
|2013-01-03|              [87.0]| 7.166666666666667|
|2013-01-04| [71.33333333333333]| 8.666666666666666|
|2013-01-05| [86.83333333333333]|               6.0|
|2013-01-06|              [82.8]|               7.0|
|2013-01-07|              [78.6]|               7.0|
|2013-01-08|[63.714285714285715]| 8.857142857142858|
|2013-01-09|             [51.25]|              14.0|
|2013-01-10|              [62.0]|              11.0|
|2013-01-11|[51.285714285714285]|15.714285714285714|
|2013-01-12|              [74.0]|              14.0|
|2013-01-13| [75.16666666666667]|15.833333333333334|
|2013-01-14| [88.16666666666667]|12.833333333333334|
|2013-01-15| [71.85714285714286]|14.714285714285714|
|2013-01-16| [86.66666666666667]|13.8333333333

In [85]:
start_date = "2017-01-02"
end_date = "2017-05-31"
date_index = pd.date_range(start_date, end_date, freq='D')

num_days = len(date_index)
random_humidities = np.random.normal(loc=mean_humidity, scale=stddev_humidity, size=num_days)

# Ensure humidity values are within a realistic range (e.g., 0 to 100)
random_humidities = np.clip(random_humidities, 0, 100)

# Create a Pandas DataFrame with the date range and generated humidity values
pandas_df = pd.DataFrame({
    'date': date_index,
    'humidity': random_humidities
})

pandas_df

date   humidity
0   2017-01-02  85.810446
1   2017-01-03  42.897725
2   2017-01-04  79.531400
3   2017-01-05  61.296704
4   2017-01-06  59.496869
..         ...        ...
145 2017-05-27  41.566020
146 2017-05-28  65.443639
147 2017-05-29  32.648288
148 2017-05-30  38.205081
149 2017-05-31  71.654762

[150 rows x 2 columns]

In [86]:
new_data = spark.createDataFrame(pandas_df)

# Convert 'date' to the proper date type
new_data = new_data.withColumn('date', to_date(new_data.date))

# Prepare the features using VectorAssembler
assembler = VectorAssembler(inputCols=["humidity"], outputCol="features")
new_data = assembler.transform(new_data)

In [87]:
# Predict using the model
predicted_data = model.transform(new_data)
generated_data = predicted_data.select('date', 'humidity', 'prediction')
generated_data.show()

+----------+------------------+------------------+
|      date|          humidity|        prediction|
+----------+------------------+------------------+
|2017-01-02|  85.8104461576719|19.220396551247546|
|2017-01-03|42.897724681400206|29.975035310839633|
|2017-01-04| 79.53140011148133| 20.79402948941867|
|2017-01-05|61.296703957671596|25.363946364385065|
|2017-01-06|59.496868555589295|25.815014926578762|
|2017-01-07| 74.87113845831932|21.961968246988498|
|2017-01-08| 32.51928746582976| 32.57604357372234|
|2017-01-09| 99.74568334497192|15.727995304649504|
|2017-01-10| 72.64141714399263|22.520773338933225|
|2017-01-11| 69.06981695512548|23.415875502197245|
|2017-01-12| 51.92897408001305|27.711654628177254|
|2017-01-13| 83.16329504447096|19.883816464623816|
|2017-01-14| 62.51019100481006|25.059826411549295|
|2017-01-15| 32.55621322251671| 32.56678936750025|
|2017-01-16| 59.33272323627739|25.856152462315187|
|2017-01-17| 61.68899069726684|25.265632810049954|
|2017-01-18| 73.35311260040162|

In [88]:
generated_data = generated_data.withColumnRenamed("prediction","meantemp")

In [89]:
generated_data.show()

+----------+------------------+------------------+
|      date|          humidity|          meantemp|
+----------+------------------+------------------+
|2017-01-02|  85.8104461576719|19.220396551247546|
|2017-01-03|42.897724681400206|29.975035310839633|
|2017-01-04| 79.53140011148133| 20.79402948941867|
|2017-01-05|61.296703957671596|25.363946364385065|
|2017-01-06|59.496868555589295|25.815014926578762|
|2017-01-07| 74.87113845831932|21.961968246988498|
|2017-01-08| 32.51928746582976| 32.57604357372234|
|2017-01-09| 99.74568334497192|15.727995304649504|
|2017-01-10| 72.64141714399263|22.520773338933225|
|2017-01-11| 69.06981695512548|23.415875502197245|
|2017-01-12| 51.92897408001305|27.711654628177254|
|2017-01-13| 83.16329504447096|19.883816464623816|
|2017-01-14| 62.51019100481006|25.059826411549295|
|2017-01-15| 32.55621322251671| 32.56678936750025|
|2017-01-16| 59.33272323627739|25.856152462315187|
|2017-01-17| 61.68899069726684|25.265632810049954|
|2017-01-18| 73.35311260040162|

In [90]:
final_df = df.unionByName(generated_data)
final_df.show()

+----------+------------------+------------------+
|      date|          meantemp|          humidity|
+----------+------------------+------------------+
|2013-01-01|              10.0|              84.5|
|2013-01-02|               7.4|              92.0|
|2013-01-03| 7.166666666666667|              87.0|
|2013-01-04| 8.666666666666666| 71.33333333333333|
|2013-01-05|               6.0| 86.83333333333333|
|2013-01-06|               7.0|              82.8|
|2013-01-07|               7.0|              78.6|
|2013-01-08| 8.857142857142858|63.714285714285715|
|2013-01-09|              14.0|             51.25|
|2013-01-10|              11.0|              62.0|
|2013-01-11|15.714285714285714|51.285714285714285|
|2013-01-12|              14.0|              74.0|
|2013-01-13|15.833333333333334| 75.16666666666667|
|2013-01-14|12.833333333333334| 88.16666666666667|
|2013-01-15|14.714285714285714| 71.85714285714286|
|2013-01-16|13.833333333333334| 86.66666666666667|
|2013-01-17|              16.5|

## Introducing the price column for prediction purposes

* The price increases with temperature, assuming higher temperatures lead to higher demand for cooling appliances
* The price decreases with humidity, assuming higher humidity reduces the efficiency of cooling, thus affecting prices.


* Price increases by 1 dollar for every degree Celsius above a baseline temperature of 20°C
* Price decreases by 0.5 dollar for every percentage point of humidity above a baseline of 50%.

In [91]:
baseline_temp = 20.0
baseline_humidity = 50.0

In [92]:
final_df = final_df.withColumn("price", 
                   when(col("meantemp") > baseline_temp, (col("meantemp") - baseline_temp) * 1) \
                   .otherwise(0) - \
                   when(col("humidity") > baseline_humidity, (col("humidity") - baseline_humidity) * 0.5) \
                   .otherwise(0)
                  )

# Adjust price to have a base price of $50
final_df = final_df.withColumn("price", col("price") + 50)

final_df.show()

+----------+------------------+------------------+------------------+
|      date|          meantemp|          humidity|             price|
+----------+------------------+------------------+------------------+
|2013-01-01|              10.0|              84.5|             32.75|
|2013-01-02|               7.4|              92.0|              29.0|
|2013-01-03| 7.166666666666667|              87.0|              31.5|
|2013-01-04| 8.666666666666666| 71.33333333333333|39.333333333333336|
|2013-01-05|               6.0| 86.83333333333333|31.583333333333336|
|2013-01-06|               7.0|              82.8|              33.6|
|2013-01-07|               7.0|              78.6|              35.7|
|2013-01-08| 8.857142857142858|63.714285714285715| 43.14285714285714|
|2013-01-09|              14.0|             51.25|            49.375|
|2013-01-10|              11.0|              62.0|              44.0|
|2013-01-11|15.714285714285714|51.285714285714285| 49.35714285714286|
|2013-01-12|        

# Data Visualization -> Time series plot for the above data

In [93]:
pd_df = final_df.toPandas()
pd_df

date   meantemp   humidity      price
0     2013-01-01  10.000000  84.500000  32.750000
1     2013-01-02   7.400000  92.000000  29.000000
2     2013-01-03   7.166667  87.000000  31.500000
3     2013-01-04   8.666667  71.333333  39.333333
4     2013-01-05   6.000000  86.833333  31.583333
...          ...        ...        ...        ...
1607  2017-05-27  30.308783  41.566020  60.308783
1608  2017-05-28  24.324656  65.443639  46.602836
1609  2017-05-29  32.543714  32.648288  62.543714
1610  2017-05-30  31.151089  38.205081  61.151089
1611  2017-05-31  22.768046  71.654762  41.940665

[1612 rows x 4 columns]

In [94]:
pd_df['date'] = pd.to_datetime(pd_df['date'])

In [95]:
# Create a figure with subplots
fig = make_subplots(rows=3, cols=1,
                    shared_xaxes=True,
                    vertical_spacing=0.02,  # Vertical spacing between plots
                    subplot_titles=("Mean Temperature", "Humidity", "Price"))

# Temperature Plot
fig.add_trace(
    go.Scatter(x=pd_df['date'], y=pd_df['meantemp'], name='Mean Temperature', mode='lines', line=dict(color='red')),
    row=1, col=1
)

# Humidity Plot
fig.add_trace(
    go.Scatter(x=pd_df['date'], y=pd_df['humidity'], name='Humidity', mode='lines', line=dict(color='blue')),
    row=2, col=1
)

# Price Plot
fig.add_trace(
    go.Scatter(x=pd_df['date'], y=pd_df['price'], name='Price', mode='lines', line=dict(color='green')),
    row=3, col=1
)

# Update x-axis and y-axis labels
fig.update_xaxes(title_text="Date", row=3, col=1)
fig.update_yaxes(title_text="Temperature (°C)", row=1, col=1)
fig.update_yaxes(title_text="Humidity (%)", row=2, col=1)
fig.update_yaxes(title_text="Price ($)", row=3, col=1)

# Update layout and plot size
fig.update_layout(height=900, width=700, title_text="Data Over Time", showlegend=False)

# Show plot
fig.show()

In [96]:
final_df.show()

+----------+------------------+------------------+------------------+
|      date|          meantemp|          humidity|             price|
+----------+------------------+------------------+------------------+
|2013-01-01|              10.0|              84.5|             32.75|
|2013-01-02|               7.4|              92.0|              29.0|
|2013-01-03| 7.166666666666667|              87.0|              31.5|
|2013-01-04| 8.666666666666666| 71.33333333333333|39.333333333333336|
|2013-01-05|               6.0| 86.83333333333333|31.583333333333336|
|2013-01-06|               7.0|              82.8|              33.6|
|2013-01-07|               7.0|              78.6|              35.7|
|2013-01-08| 8.857142857142858|63.714285714285715| 43.14285714285714|
|2013-01-09|              14.0|             51.25|            49.375|
|2013-01-10|              11.0|              62.0|              44.0|
|2013-01-11|15.714285714285714|51.285714285714285| 49.35714285714286|
|2013-01-12|        

In [97]:
pd_final_df = final_df.toPandas()
pd_final_df

date   meantemp   humidity      price
0     2013-01-01  10.000000  84.500000  32.750000
1     2013-01-02   7.400000  92.000000  29.000000
2     2013-01-03   7.166667  87.000000  31.500000
3     2013-01-04   8.666667  71.333333  39.333333
4     2013-01-05   6.000000  86.833333  31.583333
...          ...        ...        ...        ...
1607  2017-05-27  30.308783  41.566020  60.308783
1608  2017-05-28  24.324656  65.443639  46.602836
1609  2017-05-29  32.543714  32.648288  62.543714
1610  2017-05-30  31.151089  38.205081  61.151089
1611  2017-05-31  22.768046  71.654762  41.940665

[1612 rows x 4 columns]

In [98]:
pandas_df.to_csv('C:\\Users\\Rishita\\Desktop\\Rishita Desktop Copy\\IoT_DA331_Project\\final_pd_data.csv', index=False)


# Prediction

Predicting the price of test data by training the model on the features and price of train data

In [99]:
# First, ensure 'date' is converted to a numeric feature like day of year
final_df = final_df.withColumn("day_of_year", dayofyear(col("date")))

# Prepare features and target. Update 'required_features' to include 'day_of_year' instead of 'date'
required_features = ['meantemp', 'humidity', 'day_of_year']
assembler = VectorAssembler(inputCols=required_features, outputCol="features")

# Split data
train_data, test_data = final_df.randomSplit([0.8, 0.2], seed=42)

# Train model
rf = RandomForestRegressor(featuresCol="features", labelCol="price", numTrees=100)
pipeline = Pipeline(stages=[assembler, rf])

model = pipeline.fit(train_data)

# Make predictions
predictions = model.transform(test_data)

# Select example rows to display
predictions.select("prediction", "price", "features").show(5)

# Evaluate the model using the RMSE metric
evaluator = RegressionEvaluator(labelCol="price", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions)
print("Root Mean Squared Error (RMSE) on test data =", rmse)


+------------------+------------------+--------------------+
|        prediction|             price|            features|
+------------------+------------------+--------------------+
| 32.01300017100523|              31.5|[7.16666666666666...|
| 35.70620218005661|              35.7|      [7.0,78.6,7.0]|
|46.100367349501575|            49.375|    [14.0,51.25,9.0]|
|32.129742930222314|30.916666666666664|[12.8333333333333...|
|36.277925229172546|37.357142857142854|[11.2857142857142...|
+------------------+------------------+--------------------+
only showing top 5 rows

Root Mean Squared Error (RMSE) on test data = 1.3871814083036875


# Control logic on the use of appliances

In [100]:
def control_logic(predicted_price, threshold=35.0):
    if predicted_price > threshold:
        return "Turn Off"
    else:
        return "Turn On"

# Register the UDF
control_logic_udf = udf(control_logic, StringType())

In [101]:
control_logic_udf

<function __main__.control_logic(predicted_price, threshold=35.0)>

In [102]:
# Assuming 'predictions' DataFrame has a column 'prediction' which contains predicted prices
predictions = predictions.withColumn("action", control_logic_udf(predictions["prediction"]))

In [103]:
predictions.show()

+----------+------------------+------------------+------------------+-----------+--------------------+------------------+--------+
|      date|          meantemp|          humidity|             price|day_of_year|            features|        prediction|  action|
+----------+------------------+------------------+------------------+-----------+--------------------+------------------+--------+
|2013-01-03| 7.166666666666667|              87.0|              31.5|          3|[7.16666666666666...| 32.01300017100523| Turn On|
|2013-01-07|               7.0|              78.6|              35.7|          7|      [7.0,78.6,7.0]| 35.70620218005661|Turn Off|
|2013-01-09|              14.0|             51.25|            49.375|          9|    [14.0,51.25,9.0]|46.100367349501575|Turn Off|
|2013-01-14|12.833333333333334| 88.16666666666667|30.916666666666664|         14|[12.8333333333333...|32.129742930222314| Turn On|
|2013-01-20|11.285714285714286| 75.28571428571429|37.357142857142854|         20|[1

In [104]:
predictions.select("prediction", "action").show()

+------------------+--------+
|        prediction|  action|
+------------------+--------+
| 32.01300017100523| Turn On|
| 35.70620218005661|Turn Off|
|46.100367349501575|Turn Off|
|32.129742930222314| Turn On|
|36.277925229172546|Turn Off|
| 44.70549815307738|Turn Off|
| 38.82723587023231|Turn Off|
| 33.58597801165075| Turn On|
| 42.26765474912164|Turn Off|
| 32.92015624569557| Turn On|
| 32.92015624569557| Turn On|
| 35.12900632682832|Turn Off|
|42.179496936193225|Turn Off|
| 39.12488855936226|Turn Off|
| 39.76185528598711|Turn Off|
| 46.33910066800197|Turn Off|
|  42.4175812060317|Turn Off|
|  60.0247364571376|Turn Off|
| 59.55843926080795|Turn Off|
| 60.92996482814053|Turn Off|
+------------------+--------+
only showing top 20 rows



# Plot

In [105]:
data = predictions.toPandas()
data['date'] = pd.to_datetime(data['date'])  # ensure 'date' is datetime type
data

date   meantemp   humidity      price  day_of_year  \
0   2013-01-03   7.166667  87.000000  31.500000            3   
1   2013-01-07   7.000000  78.600000  35.700000            7   
2   2013-01-09  14.000000  51.250000  49.375000            9   
3   2013-01-14  12.833333  88.166667  30.916667           14   
4   2013-01-20  11.285714  75.285714  37.357143           20   
..         ...        ...        ...        ...          ...   
278 2017-05-13  23.857662  67.307019  45.204152          133   
279 2017-05-21  24.479428  64.826074  47.066390          141   
280 2017-05-24  27.549318  52.576721  56.260958          144   
281 2017-05-28  24.324656  65.443639  46.602836          148   
282 2017-05-30  31.151089  38.205081  61.151089          150   

                                           features  prediction    action  
0                    [7.166666666666667, 87.0, 3.0]   32.013000   Turn On  
1                                  [7.0, 78.6, 7.0]   35.706202  Turn Off  
2                                [14.0, 51.25, 9.0]   46.100367  Turn Off  
3     [12.833333333333334, 88.16666666666667, 14.0]   32.129743   Turn On  
4     [11.285714285714286, 75.28571428571429, 20.0]   36.277925  Turn Off  
..                                              ...         ...       ...  
278  [23.857661810450857, 67.30701922459188, 133.0]   45.441051  Turn Off  
279   [24.47942766189261, 64.82607445249718, 141.0]   47.111237  Turn Off  
280  [27.549318403863857, 52.57672146932049, 144.0]   57.116932  Turn Off  
281  [24.324655674802674, 65.44363933057325, 148.0]   46.909308  Turn Off  
282   [31.15108947090993, 38.20508127977082, 150.0]   61.250215  Turn Off  

[283 rows x 8 columns]

In [106]:
# Create a subplot with 3 rows
fig = make_subplots(
    rows=3, cols=1,
    shared_xaxes=True,
    vertical_spacing=0.1,
    subplot_titles=("Mean Temperature (°C)", "Humidity (%)", "Price ($) with Action Indicators")
)

# Mean Temperature Trace
fig.add_trace(
    go.Scatter(x=data['date'], y=data['meantemp'], name='Mean Temperature', marker=dict(color='red')),
    row=1, col=1
)

# Humidity Trace
fig.add_trace(
    go.Scatter(x=data['date'], y=data['humidity'], name='Humidity', marker=dict(color='blue')),
    row=2, col=1
)

# Price Trace with Actions
colors = [ 'green' if action == 'Turn On' else 'red' for action in data['action']]
fig.add_trace(
    go.Scatter(x=data['date'], y=data['price'], name='Price',
               mode='lines+markers', marker=dict(color=colors, size=5)),
    row=3, col=1
)

# Update x-axis and y-axis labels
fig.update_xaxes(title_text="Date", row=3, col=1)
fig.update_yaxes(title_text="°C", row=1, col=1)
fig.update_yaxes(title_text="%", row=2, col=1)
fig.update_yaxes(title_text="$", row=3, col=1)

# Update the layout and add titles
fig.update_layout(
    height=900,  # Height in pixels
    width=1000,  # Width in pixels
    title_text="Temperature, Humidity, and Price Over Time with Action Indicators",
    showlegend=True
)

# Show the plot
fig.show()


In [107]:
# Create subplots with 2 y-axes on the left and 1 on the right
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Mean Temperature Trace
fig.add_trace(
    go.Scatter(x=data['date'], y=data['meantemp'], name='Mean Temperature (°C)', marker=dict(color='red')),
    secondary_y=False,
)

# Humidity Trace
fig.add_trace(
    go.Scatter(x=data['date'], y=data['humidity'], name='Humidity (%)', marker=dict(color='blue')),
    secondary_y=True,
)

# Price Trace with Actions
fig.add_trace(
    go.Scatter(x=data['date'], y=data['price'], name='Price ($)', mode='lines+markers',
               marker=dict(color=[{'Turn On': 'green', 'Turn Off': 'red'}[action] for action in data['action']])),
    secondary_y=True,
)

# Set x-axis title
fig.update_xaxes(title_text="Date")

# Set y-axes titles
fig.update_yaxes(title_text="Mean Temperature (°C) / Humidity (%)", secondary_y=False)
fig.update_yaxes(title_text="Price ($)", secondary_y=True)

# Add figure title and layout adjustments
fig.update_layout(
    title_text="Temperature, Humidity, and Price Over Time with Action Indicators",
    legend_title="Legend",
    height=600,
    width=1000
)

# Show plot
fig.show()


# Part 2 -> Intra day weather conditions to keep the cost consumption below the threshold

## Data generation

In [108]:
data_path = "C:\\Users\\Rishita\\Desktop\\Rishita Desktop Copy\\IoT_DA331_Project\\weather_madrid_2019-2022.csv"
df = spark.read.csv(data_path, header=True, inferSchema=True)
df.show()

+---+-------------------+-----------+----------+--------------+--------+-------------------+---------------+-------------+
|_c0|               time|temperature|wind_speed|wind_direction|humidity|barometric_pressure|solar_radiation|precipitation|
+---+-------------------+-----------+----------+--------------+--------+-------------------+---------------+-------------+
|  0|2019-01-01 00:59:59|        3.1|      0.65|          64.0|    50.0|              949.0|            0.0|          0.0|
|  1|2019-01-01 01:59:59|        2.9|      0.95|          32.0|    49.0|              949.0|            0.0|          0.0|
|  2|2019-01-01 02:59:59|        3.1|      0.87|          62.0|    46.0|              949.0|            0.0|          0.0|
|  3|2019-01-01 03:59:59|        1.9|      0.73|          75.0|    51.0|              949.0|            0.0|          0.0|
|  4|2019-01-01 04:59:59|        0.7|      0.57|          53.0|    56.0|              949.0|            0.0|          0.0|
|  5|2019-01-01 

In [109]:
df.printSchema()

root
 |-- _c0: integer (nullable = true)
 |-- time: timestamp (nullable = true)
 |-- temperature: double (nullable = true)
 |-- wind_speed: double (nullable = true)
 |-- wind_direction: double (nullable = true)
 |-- humidity: double (nullable = true)
 |-- barometric_pressure: double (nullable = true)
 |-- solar_radiation: double (nullable = true)
 |-- precipitation: double (nullable = true)



In [110]:
df = df.drop('wind_speed','wind_direction','solar_radiation','precipitation', '_c0','barometric_pressure')
df.show()

+-------------------+-----------+--------+
|               time|temperature|humidity|
+-------------------+-----------+--------+
|2019-01-01 00:59:59|        3.1|    50.0|
|2019-01-01 01:59:59|        2.9|    49.0|
|2019-01-01 02:59:59|        3.1|    46.0|
|2019-01-01 03:59:59|        1.9|    51.0|
|2019-01-01 04:59:59|        0.7|    56.0|
|2019-01-01 05:59:59|        0.5|    53.0|
|2019-01-01 06:59:59|        0.0|    55.0|
|2019-01-01 07:59:59|       -0.8|    60.0|
|2019-01-01 08:59:59|        0.0|    56.0|
|2019-01-01 09:59:59|        2.2|    48.0|
|2019-01-01 10:59:59|        3.1|    47.0|
|2019-01-01 11:59:59|        5.5|    39.0|
|2019-01-01 12:59:59|        7.8|    34.0|
|2019-01-01 13:59:59|       10.1|    31.0|
|2019-01-01 14:59:59|       10.4|    33.0|
|2019-01-01 15:59:59|       11.9|    30.0|
|2019-01-01 16:59:59|       10.1|    35.0|
|2019-01-01 17:59:59|        8.5|    38.0|
|2019-01-01 18:59:59|        7.7|    39.0|
|2019-01-01 19:59:59|        7.1|    43.0|
+----------

## Dividing into training and testing data

In [111]:
# Calculate the row count
total_rows = df.count()
train_rows = int(total_rows * 0.8)
test_rows = total_rows - train_rows

# Adding an incremental index to each row
df = df.withColumn("row_index", row_number().over(Window.orderBy("time")))

# Splitting the data
train_df = df.filter(col("row_index") <= train_rows).drop("row_index")
test_df = df.filter(col("row_index") > train_rows).drop("row_index")

# Show split info
print(f"Total rows: {total_rows}, Training rows: {train_rows}, Testing rows: {test_rows}")
train_df.show()

# Save the test data
test_df = test_df.drop("humidity")
test_df.show()

Total rows: 27024, Training rows: 21619, Testing rows: 5405
+-------------------+-----------+--------+
|               time|temperature|humidity|
+-------------------+-----------+--------+
|2019-01-01 00:59:59|        3.1|    50.0|
|2019-01-01 01:59:59|        2.9|    49.0|
|2019-01-01 02:59:59|        3.1|    46.0|
|2019-01-01 03:59:59|        1.9|    51.0|
|2019-01-01 04:59:59|        0.7|    56.0|
|2019-01-01 05:59:59|        0.5|    53.0|
|2019-01-01 06:59:59|        0.0|    55.0|
|2019-01-01 07:59:59|       -0.8|    60.0|
|2019-01-01 08:59:59|        0.0|    56.0|
|2019-01-01 09:59:59|        2.2|    48.0|
|2019-01-01 10:59:59|        3.1|    47.0|
|2019-01-01 11:59:59|        5.5|    39.0|
|2019-01-01 12:59:59|        7.8|    34.0|
|2019-01-01 13:59:59|       10.1|    31.0|
|2019-01-01 14:59:59|       10.4|    33.0|
|2019-01-01 15:59:59|       11.9|    30.0|
|2019-01-01 16:59:59|       10.1|    35.0|
|2019-01-01 17:59:59|        8.5|    38.0|
|2019-01-01 18:59:59|        7.7|    

In [112]:
test_df_pandas = test_df.toPandas()
test_df_pandas
# test_df_pandas.to_csv("C:\\Users\\Rishita\\Desktop\\Rishita Desktop Copy\\IoT_DA331_Project\\test_data.csv")
test_df_pandas.to_csv(r"C:\Users\Rishita\Desktop\Rishita Desktop Copy\IoT_DA331_Project\test_data.csv", index=False)


# Optionally save the train data
df = train_df

In [113]:
df = df.withColumn("DayOfYear", dayofyear(col("time")))
df = df.withColumn("Hour", hour(col("time")))

In [114]:
df.show()

+-------------------+-----------+--------+---------+----+
|               time|temperature|humidity|DayOfYear|Hour|
+-------------------+-----------+--------+---------+----+
|2019-01-01 00:59:59|        3.1|    50.0|        1|   0|
|2019-01-01 01:59:59|        2.9|    49.0|        1|   1|
|2019-01-01 02:59:59|        3.1|    46.0|        1|   2|
|2019-01-01 03:59:59|        1.9|    51.0|        1|   3|
|2019-01-01 04:59:59|        0.7|    56.0|        1|   4|
|2019-01-01 05:59:59|        0.5|    53.0|        1|   5|
|2019-01-01 06:59:59|        0.0|    55.0|        1|   6|
|2019-01-01 07:59:59|       -0.8|    60.0|        1|   7|
|2019-01-01 08:59:59|        0.0|    56.0|        1|   8|
|2019-01-01 09:59:59|        2.2|    48.0|        1|   9|
|2019-01-01 10:59:59|        3.1|    47.0|        1|  10|
|2019-01-01 11:59:59|        5.5|    39.0|        1|  11|
|2019-01-01 12:59:59|        7.8|    34.0|        1|  12|
|2019-01-01 13:59:59|       10.1|    31.0|        1|  13|
|2019-01-01 14

In [115]:
df_pandas = df.toPandas()
df_pandas

time  temperature  humidity  DayOfYear  Hour
0     2019-01-01 00:59:59          3.1      50.0          1     0
1     2019-01-01 01:59:59          2.9      49.0          1     1
2     2019-01-01 02:59:59          3.1      46.0          1     2
3     2019-01-01 03:59:59          1.9      51.0          1     3
4     2019-01-01 04:59:59          0.7      56.0          1     4
...                   ...          ...       ...        ...   ...
21614 2021-06-19 14:59:59         18.4      37.0        170    14
21615 2021-06-19 15:59:59         19.0      36.0        170    15
21616 2021-06-19 16:59:59         20.1      35.0        170    16
21617 2021-06-19 17:59:59         19.8      37.0        170    17
21618 2021-06-19 18:59:59         20.0      36.0        170    18

[21619 rows x 5 columns]

## Data Visualisation -> using plotly library to plot time series and other graphs

In [116]:
data = df_pandas
data

time  temperature  humidity  DayOfYear  Hour
0     2019-01-01 00:59:59          3.1      50.0          1     0
1     2019-01-01 01:59:59          2.9      49.0          1     1
2     2019-01-01 02:59:59          3.1      46.0          1     2
3     2019-01-01 03:59:59          1.9      51.0          1     3
4     2019-01-01 04:59:59          0.7      56.0          1     4
...                   ...          ...       ...        ...   ...
21614 2021-06-19 14:59:59         18.4      37.0        170    14
21615 2021-06-19 15:59:59         19.0      36.0        170    15
21616 2021-06-19 16:59:59         20.1      35.0        170    16
21617 2021-06-19 17:59:59         19.8      37.0        170    17
21618 2021-06-19 18:59:59         20.0      36.0        170    18

[21619 rows x 5 columns]

In [117]:
!pip install nbformat --upgrade


[notice] A new release of pip is available: 24.0 -> 24.3.1
[notice] To update, run: C:\Users\Rishita\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [118]:
# Create subplots
fig = make_subplots(rows=2, cols=1, shared_xaxes=True, vertical_spacing=0.1, subplot_titles=("Temperature Over Time", "Humidity Over Time"))

# Add temperature trace
fig.add_trace(
    go.Scatter(x=data['time'], y=data['temperature'], name='Temperature'),
    row=1, col=1
)

# Add humidity trace
fig.add_trace(
    go.Scatter(x=data['time'], y=data['humidity'], name='Humidity'),
    row=2, col=1
)

# Update layout
fig.update_layout(height=600, width=800, title_text="Temperature and Humidity Over Time")
fig.update_xaxes(title_text="Time", row=2, col=1)
fig.update_yaxes(title_text="Temperature (°C)", row=1, col=1)
fig.update_yaxes(title_text="Humidity (%)", row=2, col=1)

# Show plot
fig.show()

In [119]:
# Create subplots for area charts
fig = make_subplots(rows=2, cols=1, shared_xaxes=True, vertical_spacing=0.1, subplot_titles=("Temperature Over Time", "Humidity Over Time"))

# Add temperature area chart
fig.add_trace(
    go.Scatter(x=data['time'], y=data['temperature'], name='Temperature', fill='tozeroy'),
    row=1, col=1
)

# Add humidity area chart
fig.add_trace(
    go.Scatter(x=data['time'], y=data['humidity'], name='Humidity', fill='tozeroy'),
    row=2, col=1
)

# Update layout
fig.update_layout(height=600, width=800, title_text="Temperature and Humidity Over Time")
fig.update_xaxes(title_text="Time", row=2, col=1)
fig.update_yaxes(title_text="Temperature (°C)", row=1, col=1)
fig.update_yaxes(title_text="Humidity (%)", row=2, col=1)

# Show plot
fig.show()

## Observations from the above plots
1. Both the temperature and humidity exhibit clear seasonal cycles. 
2. Temperature peaks during the middle of the year and reaches its lowest points toward the beginning and end of the year, indicating typical summer and winter seasons respectively.
3. Humidity displays somewhat inverse pattern to temperature, where it tends to be lower during hot months and higher during cooler months
4. Systems need to adapt to the varying changes of tempr and humidity and thus efficiently adjust the heating and cooling systems in a cost effective way.

## Defining the model

### Since I am taking dataset of Madrid, here the cost for the appliance heaters
The following code is effectively managing energy use based on external climate conditions and internal temperature settings. Cumulative cost calculation and temperature optimization to keep the cost below a particular threshold for each day.

In [120]:
df = df.drop("humidity")
df.show()

+-------------------+-----------+---------+----+
|               time|temperature|DayOfYear|Hour|
+-------------------+-----------+---------+----+
|2019-01-01 00:59:59|        3.1|        1|   0|
|2019-01-01 01:59:59|        2.9|        1|   1|
|2019-01-01 02:59:59|        3.1|        1|   2|
|2019-01-01 03:59:59|        1.9|        1|   3|
|2019-01-01 04:59:59|        0.7|        1|   4|
|2019-01-01 05:59:59|        0.5|        1|   5|
|2019-01-01 06:59:59|        0.0|        1|   6|
|2019-01-01 07:59:59|       -0.8|        1|   7|
|2019-01-01 08:59:59|        0.0|        1|   8|
|2019-01-01 09:59:59|        2.2|        1|   9|
|2019-01-01 10:59:59|        3.1|        1|  10|
|2019-01-01 11:59:59|        5.5|        1|  11|
|2019-01-01 12:59:59|        7.8|        1|  12|
|2019-01-01 13:59:59|       10.1|        1|  13|
|2019-01-01 14:59:59|       10.4|        1|  14|
|2019-01-01 15:59:59|       11.9|        1|  15|
|2019-01-01 16:59:59|       10.1|        1|  16|
|2019-01-01 17:59:59

In [121]:
import pyspark.sql.functions as F

# Function to simulate cost based on room and external temperatures
def calculate_cost(room_temp, outside_temp):
    # The coefficient increases as the difference between room and outside temperature increases
    temp_diff = room_temp - outside_temp
    return (0.05 * temp_diff ** 2)

# Register UDF
calculate_cost_udf = udf(calculate_cost, DoubleType())

# Assuming initial room temperature
initial_room_temperature = 22.0

# Add a column for simulated costs
df = df.withColumn("predicted_cost", calculate_cost_udf(F.lit(initial_room_temperature), col("temperature")))

# Define a threshold for daily costs
daily_threshold = 10.0  # Adjust as necessary

# Window specification for cumulative cost
windowSpec = Window.partitionBy("DayOfYear").orderBy("time").rowsBetween(Window.unboundedPreceding, 0)

# Calculate cumulative cost for each hour
df = df.withColumn("cumulative_cost", F.sum("predicted_cost").over(windowSpec))

# Optimization logic to find optimal room temperature
def optimize_temperature(cumulative_cost, room_temp, outside_temp, step=0.1, max_iter=100):
    iteration = 0
    while cumulative_cost > daily_threshold and iteration < max_iter:
        room_temp -= step  # Adjust temperature
        # Recalculate cost with new temperature
        cumulative_cost -= calculate_cost(room_temp, outside_temp)  # Assuming constant humidity for simplification
        iteration += 1
    return room_temp

# Register the optimization UDF
optimize_temperature_udf = udf(optimize_temperature, DoubleType())

# Apply the UDF to adjust the room temperature
df = df.withColumn("optimal_temperature", optimize_temperature_udf(col("cumulative_cost"), F.lit(initial_room_temperature), col("temperature")))

# Show the results
df.select("DayOfYear", "time", "temperature","predicted_cost", "cumulative_cost", "optimal_temperature").show()


+---------+-------------------+-----------+------------------+------------------+-------------------+
|DayOfYear|               time|temperature|    predicted_cost|   cumulative_cost|optimal_temperature|
+---------+-------------------+-----------+------------------+------------------+-------------------+
|        1|2019-01-01 00:59:59|        3.1|           17.8605|           17.8605|               21.9|
|        1|2019-01-01 01:59:59|        2.9|18.240500000000004|            36.101| 21.799999999999997|
|        1|2019-01-01 02:59:59|        3.1|           17.8605|           53.9615| 21.699999999999996|
|        1|2019-01-01 03:59:59|        1.9|20.200500000000005|            74.162| 21.599999999999994|
|        1|2019-01-01 04:59:59|        0.7|22.684500000000003|           96.8465| 21.599999999999994|
|        1|2019-01-01 05:59:59|        0.5|           23.1125|           119.959| 21.499999999999993|
|        1|2019-01-01 06:59:59|        0.0|24.200000000000003|           144.159| 

## Generated the final training data file!

In [122]:
final_data = df.select("time","temperature","optimal_temperature")
final_data.show()

+-------------------+-----------+-------------------+
|               time|temperature|optimal_temperature|
+-------------------+-----------+-------------------+
|2019-01-01 00:59:59|        3.1|               21.9|
|2019-01-01 01:59:59|        2.9| 21.799999999999997|
|2019-01-01 02:59:59|        3.1| 21.699999999999996|
|2019-01-01 03:59:59|        1.9| 21.599999999999994|
|2019-01-01 04:59:59|        0.7| 21.599999999999994|
|2019-01-01 05:59:59|        0.5| 21.499999999999993|
|2019-01-01 06:59:59|        0.0|  21.39999999999999|
|2019-01-01 07:59:59|       -0.8|  21.29999999999999|
|2019-01-01 08:59:59|        0.0|  21.19999999999999|
|2019-01-01 09:59:59|        2.2| 20.799999999999983|
|2019-01-01 10:59:59|        3.1|  20.59999999999998|
|2019-01-01 11:59:59|        5.5|  19.99999999999997|
|2019-01-01 12:59:59|        7.8| 18.899999999999956|
|2019-01-01 13:59:59|       10.1| 15.399999999999919|
|2019-01-01 14:59:59|       10.4|  11.99999999999993|
|2019-01-01 15:59:59|       

In [131]:
processed = final_data.toPandas()
processed.to_csv("C:\\Users\\Rishita\\Desktop\\Rishita Desktop Copy\\IoT_DA331_Project\\processed_data.csv", index=False)

### Trying with a different threshold cost of 2 dollars each day

In [125]:
df.printSchema()

root
 |-- time: timestamp (nullable = true)
 |-- temperature: double (nullable = true)
 |-- DayOfYear: integer (nullable = true)
 |-- Hour: integer (nullable = true)
 |-- predicted_cost: double (nullable = true)
 |-- cumulative_cost: double (nullable = true)
 |-- optimal_temperature: double (nullable = true)



In [126]:
new_df = df

#### The code below is now simply creating another column for updated predicted price based on the temperature difference between optimal temperature that is found above and external temperature, the updated predicted price is the price that the user is paying for that hour and updated cumulative price is the one that the user is paying daily

In [127]:

# Define the UDF to recalculate cost based on the adjusted optimal temperature
def recalculate_cost(opt_temp, outside_temp):
    # Simulate the recalculation of cost based on the new optimal temperature
    # Modify this function according to your specific cost calculation logic
    temp_diff = opt_temp - outside_temp
    return (0.05 * temp_diff ** 2)

recalculate_cost_udf = udf(recalculate_cost, DoubleType())

# Recalculate predicted cost using the optimal temperature
new_df = new_df.withColumn("updated_predicted_cost", recalculate_cost_udf(col("optimal_temperature"),col("temperature")))

# Update the cumulative cost to reflect the cost with the new temperature
# Redefine the window specification for cumulative cost calculation
windowSpec = Window.partitionBy("DayOfYear").orderBy("time").rowsBetween(Window.unboundedPreceding, 0)

# Calculate the updated cumulative cost for each hour using the newly predicted cost
new_df = new_df.withColumn("updated_cumulative_cost", _sum("updated_predicted_cost").over(windowSpec))

# Add logic to check and update costs only if the new cumulative cost is less than the threshold
new_df = new_df.withColumn("final_cumulative_cost",
                   when(col("updated_cumulative_cost") <= daily_threshold, col("updated_cumulative_cost"))
                   .otherwise(col("cumulative_cost")))


In [128]:
new_df.printSchema()

root
 |-- time: timestamp (nullable = true)
 |-- temperature: double (nullable = true)
 |-- DayOfYear: integer (nullable = true)
 |-- Hour: integer (nullable = true)
 |-- predicted_cost: double (nullable = true)
 |-- cumulative_cost: double (nullable = true)
 |-- optimal_temperature: double (nullable = true)
 |-- updated_predicted_cost: double (nullable = true)
 |-- updated_cumulative_cost: double (nullable = true)
 |-- final_cumulative_cost: double (nullable = true)



In [129]:
new_df.select("updated_predicted_cost").show()

+----------------------+
|updated_predicted_cost|
+----------------------+
|    17.671999999999993|
|               17.8605|
|     17.29799999999999|
|     19.40449999999999|
|     21.84049999999999|
|    22.049999999999986|
|    22.897999999999982|
|     24.42049999999998|
|     22.47199999999998|
|     17.29799999999997|
|    15.312499999999964|
|     10.51249999999996|
|     6.160499999999951|
|     1.404499999999957|
|   0.12799999999998887|
|  4.999999999993037E-4|
|    0.5444999999999757|
|    4.1404999999999434|
|     5.512499999999944|
|     6.497999999999944|
+----------------------+
only showing top 20 rows



In [130]:
new_df.select("updated_cumulative_cost").show()

+-----------------------+
|updated_cumulative_cost|
+-----------------------+
|     17.671999999999993|
|      35.53249999999999|
|      52.83049999999999|
|      72.23499999999999|
|      94.07549999999998|
|     116.12549999999996|
|     139.02349999999996|
|     163.44399999999993|
|      185.9159999999999|
|     203.21399999999988|
|     218.52649999999986|
|     229.03899999999982|
|     235.19949999999977|
|     236.60399999999973|
|     236.73199999999972|
|      236.7324999999997|
|     237.27699999999967|
|     241.41749999999962|
|     246.92999999999955|
|     253.42799999999949|
+-----------------------+
only showing top 20 rows

